In [115]:
class superelliptic:
    def __init__(self, f, m, p):
        Rx.<x> = PolynomialRing(GF(p))
        self.polynomial = Rx(f)
        self.exponent = m
        self.characteristic = p
        
    def __repr__(self):
        f = self.polynomial
        m = self.exponent
        p = self.characteristic
        return 'Superelliptic curve with the equation y^' + str(m) + ' = ' + str(f)+' over finite field with ' + str(p) + ' elements.'
    
    def genus(self):
        r = self.polynomial.degree()
        m = self.exponent
        delta = GCD(r, m)
        return 1/2*((r-1)*(m-1) - delta + 1)
    
    def basis_holomorphic_differentials(self, j = 'all'):
        f = self.polynomial
        m = self.exponent
        p = self.characteristic
        r = f.degree()
        delta = GCD(r, m)
        Rxy.<x, y> = PolynomialRing(GF(p), 2)
        Fxy = FractionField(Rxy)
        
        basis = {}
        k = 0
        if j == 'all':
            for j in range(1, m):
                for i in range(1, r):
                    if (r*j - m*i >= delta):
                        basis[k] = superelliptic_form(self, Fxy(x^(i-1)/y^j))
                        k = k+1
            return basis
        else:
            for i in range(1, r):
                if (r*j - m*i >= delta):
                    basis[k] = superelliptic_form(self, Fxy(x^(i-1)/y^j))
                    k = k+1
            return basis
     
    def degree_and_basis_de_rham(self, j = 'all'):
        f = self.polynomial
        m = self.exponent
        p = self.characteristic
        r = f.degree()
        delta = GCD(r, m)
        Rx.<x> = PolynomialRing(GF(p))
        Rxy.<x, y> = PolynomialRing(GF(p), 2)
        Fxy = FractionField(Rxy)
        basis = {}
        degrees0 = {}
        degrees1 = {}
        t = 0
        if j == 'all':
            for j in range(1, m):
                holo = C.basis_holomorphic_differentials(j)
                for k in range(0, len(holo)):
                    basis[t] = superelliptic_cech(self, holo[k], superelliptic_function(self, Rx(0))) 
                    g = Rx(holo[k].jth_component(j))
                    degrees0[t] = (g.degree(), j)
                    t += 1
                for i in range(1, r):
                    if (r*(m-j) - m*i >= delta):
                        s = Rx(m-j)*Rx(x)*Rx(f.derivative()) - Rx(m)*Rx(i)*f
                        psi = Rx(cut(s, i))
                        basis[t] = superelliptic_cech(self, superelliptic_form(self, Fxy(psi/y^j)), superelliptic_function(self, Fxy(m*y^j/x^i)))
                        degrees0[t] = (psi.degree(), j)
                        degrees1[t] = (-i, j)
                        t += 1
            return basis, degrees0, degrees1
        
    def degree_de_rham(self, i, j='all'):
        basis, degrees0, degrees1 = self.degree_and_basis_de_rham(j)
        if i==0:
            return degrees0
        
        if i==1:
            return degrees1
        
    def basis_de_rham(self, j = 'all'):    
        basis, degrees0, degrees1 = self.degree_and_basis_de_rham(j)
        return basis
        
def reduction(C, g):
    p = C.characteristic
    Rxy.<x, y> = PolynomialRing(GF(p), 2)
    Fxy = FractionField(Rxy)
    f = C.polynomial
    r = f.degree()
    m = C.exponent
    g = Fxy(g)
    g1 = g.numerator()
    g2 = g.denominator()
    
    Rx.<x> = PolynomialRing(GF(p))
    Fx = FractionField(Rx)
    FxRy.<y> = PolynomialRing(Fx)    
    (A, B, C) = xgcd(FxRy(g2), FxRy(y^m - f))
    g = FxRy(g1*B/A)
    
    while(g.degree(Rxy(y)) >= m):
        d = g.degree(Rxy(y))
        G = coff(g, d)
        i = floor(d/m)
        g = g - G*y^d + f^i * y^(d%m) *G
    
    return(FxRy(g))

def reduction_form(C, g):
    p = C.characteristic
    Rxy.<x, y> = PolynomialRing(GF(p), 2)
    Fxy = FractionField(Rxy)
    f = C.polynomial
    r = f.degree()
    m = C.exponent
    g = reduction(C, g)

    g1 = Rxy(0)
    Rx.<x> = PolynomialRing(GF(p))
    Fx = FractionField(Rx)
    FxRy.<y> = PolynomialRing(Fx)
    
    g = FxRy(g)
    for j in range(0, m):
        if j==0:
            G = coff(g, 0)
            g1 += FxRy(G)
        else:
            G = coff(g, j)
            g1 += Fxy(y^(j-m)*f*G)
    return(g1)
        
class superelliptic_function:
    def __init__(self, C, g):
        p = C.characteristic
        Rxy.<x, y> = PolynomialRing(GF(p), 2)
        Fxy = FractionField(Rxy)
        f = C.polynomial
        r = f.degree()
        m = C.exponent
        
        self.curve = C
        g = reduction(C, g)
        self.function = g
        
    def __repr__(self):
        return str(self.function)
    
    def jth_component(self, j):
        g = self.function
        C = self.curve
        p = C.characteristic
        Rx.<x> = PolynomialRing(GF(p))
        Fx.<x> = FractionField(Rx)
        FxRy.<y> = PolynomialRing(Fx)
        g = FxRy(g)
        return coff(g, j)
    
    def __add__(self, other):
        C = self.curve
        g1 = self.function
        g2 = other.function
        g = reduction(C, g1 + g2)
        return superelliptic_function(C, g)
    
    def __sub__(self, other):
        C = self.curve
        g1 = self.function
        g2 = other.function
        g = reduction(C, g1 - g2)
        return superelliptic_function(C, g)
    
    def __mul__(self, other):
        C = self.curve
        g1 = self.function
        g2 = other.function
        g = reduction(C, g1 * g2)
        return superelliptic_function(C, g)
    
    def __truediv__(self, other):
        C = self.curve
        g1 = self.function
        g2 = other.function
        g = reduction(C, g1 / g2)
        return superelliptic_function(C, g)
    
def diffn(self):
    C = self.curve
    f = C.polynomial
    m = C.exponent
    p = C.characteristic
    g = self.function
    Rxy.<x, y> = PolynomialRing(GF(p), 2)
    Fxy = FractionField(Rxy)
    g = Fxy(g)
    A = g.derivative(x)
    B = g.derivative(y)*f.derivative(x)/(m*y^(m-1))
    return superelliptic_form(C, A+B)
        
class superelliptic_form:
    def __init__(self, C, g):
        p = C.characteristic
        Rxy.<x, y> = PolynomialRing(GF(p), 2)
        Fxy = FractionField(Rxy)
        g = Fxy(reduction_form(C, g))
        self.form = g
        self.curve = C      
        
    def __add__(self, other):
        C = self.curve
        g1 = self.form
        g2 = other.form
        g = reduction(C, g1 + g2)
        return superelliptic_form(C, g)
    
    def __sub__(self, other):
        C = self.curve
        g1 = self.form
        g2 = other.form
        g = reduction(C, g1 - g2)
        return superelliptic_form(C, g)
    
    def __repr__(self):
        g = self.form
        if len(str(g)) == 1:
            return str(g) + ' dx'
        return '('+str(g) + ') dx'
    
    def jth_component(self, j):
        g = self.form
        C = self.curve
        p = C.characteristic
        Rx.<x> = PolynomialRing(GF(p))
        Fx = FractionField(Rx)
        FxRy.<y> = PolynomialRing(Fx)
        Fxy = FractionField(FxRy)
        Ryinv.<y_inv> = PolynomialRing(Fx)
        g = Fxy(g)
        g = g(y = 1/y_inv)
        g = Ryinv(g)
        return coff(g, j)
    
    def is_regular_on_U0(self):
        C = self.curve
        p = C.characteristic
        m = C.exponent
        Rx.<x> = PolynomialRing(GF(p))
        for j in range(1, m):
            if self.jth_component(j) not in Rx:
                return 0
        return 1
    
    def is_regular_on_Uinfty(self):
        C = self.curve
        p = C.characteristic
        m = C.exponent
        f = C.polynomial
        r = f.degree()
        delta = GCD(m, r)
        M = m/delta
        R = r/delta
        
        for j in range(1, m):
            A = self.jth_component(j)
            d = degree_of_rational_fctn(A)
            if(-d*M + j*R -(M+1)<0):
                return 0
        return 1
    
    
class superelliptic_cech:
    def __init__(self, C, omega, fct):
        self.omega0 = omega
        self.omega8 = omega - diffn(fct)
        self.f = fct
        self.curve = C
        
    def __add__(self, other):
        C = self.curve
        return superelliptic_cech(C, self.omega0 + other.omega0, self.f + other.f)
    
    def __sub__(self, other):
        C = self.curve
        return superelliptic_cech(C, self.omega0 - other.omega0, self.f - other.f)
    
    def mult(self, constant):
        C = self.curve
        w1 = self.omega0.form
        f1 = self.f.function
        w2 = superelliptic_form(C, constant*w1)
        f2 = superelliptic_function(C, constant*f1)
        return superelliptic_cech(C, w2, f2)
    
    def __repr__(self):
        return "(" + str(self.omega0) + ", " + str(self.f) + ", " + str(self.omega8) + ")" 
    
    def basis_coeffs(self):
        C = self.curve
        g = self.f
        basis = C.basis_de_rham()

    def coordinates(self):
        print(self)
        C = self.curve
        p = C.characteristic
        m = C.exponent
        Rx.<x> = PolynomialRing(GF(p))
        Fx = FractionField(Rx)
        FxRy.<y> = PolynomialRing(Fx)
        g = C.genus()
        degrees0 = C.degree_de_rham(0)
        degrees0_inv = {b:a for a, b in degrees0.items()}        
        degrees1 = C.degree_de_rham(1)
        degrees1_inv = {b:a for a, b in degrees1.items()}
        basis = C.basis_de_rham()
        
        omega = self.omega0
        fct = self.f
        
        if fct.function == Rx(0) and omega.form == Rx(0):
            for j in range(1, m):
                omega_j = Fx(omega.jth_component(j))
                if omega_j != Fx(0):
                    d = d = degree_of_rational_fctn(omega_j)
                    index = degrees0_inv[(d, j)]
                    a = coeff_of_rational_fctn(omega_j)
                    a1 = coeff_of_rational_fctn(basis[index].omega0.jth_component(j))
                    elt = self - basis[index].mult(a/a1)
                    return elt.coordinates() + a/a1*vector([GF(p)(i == index) for i in range(0, 2*g)])
                    
        for j in range(1, m):
            fct_j = Fx(fct.jth_component(j))
            if (fct_j != Rx(0)):
                d = degree_of_rational_fctn(fct_j)
            
                if (d, j) in degrees1.values():
                    index = degrees1_inv[(d, j)]
                    a = coeff_of_rational_fctn(fct_j)
                    a1 = coeff_of_rational_fctn(basis[index].f.jth_component(j))
                    elt = self - basis[index].mult(a/a1)
                    return elt.coordinates() + a/a1*vector([GF(p)(i == index) for i in range(0, 2*g)])
                
                if d<0:
                    a = coeff_of_rational_fctn(fct_j)
                    elt =- superelliptic_cech(C, elt.omega0, elt.f - FxRy(y^j*x^d)).mult(a)
                    return elt.coordinates()
            
                if (fct_j != Rx(0)):
                    G = superelliptic_function(C, y^j*x^d)
                    a = coeff_of_rational_fctn(fct_j)
                    elt =-superelliptic_cech(diffn(G), G).mult(a)
                    return elt.coordinates()

        return vector(2*g*[0])
        
def degree_of_rational_fctn(f):
    Rx.<x> = PolynomialRing(GF(p))
    Fx = FractionField(Rx)
    f = Fx(f)
    f1 = f.numerator()
    f2 = f.denominator()
    d1 = f1.degree()
    d2 = f2.degree()
    return(d1 - d2)

def coeff_of_rational_fctn(f):
    Rx.<x> = PolynomialRing(GF(p))
    Fx = FractionField(Rx)
    f = Fx(f)
    f1 = f.numerator()
    f2 = f.denominator()
    d1 = f1.degree()
    d2 = f2.degree()
    a1 = f1.coefficients(sparse = false)[d1]
    a2 = f2.coefficients(sparse = false)[d2]
    return(a1/a2)

def coff(f, d):
    lista = f.coefficients(sparse = false)
    if len(lista) <= d:
        return 0
    return lista[d]

def cut(f, i):
    R = f.parent()
    coeff = f.coefficients(sparse = false)
    return sum(R(x^(j-i-1)) * coeff[j] for j in range(i+1, f.degree() + 1))

In [116]:
p = 5
C = superelliptic(x^3 + x + 2, 7, p)
C.basis_de_rham()
#C.basis_holomorphic_differentials()

{0: ((x/y) dx, 2/x*y, ((x^3*y^5 - x^3 + x - 1)/(x^2*y^6)) dx),
 1: (((-1)/y) dx, 2/x^2*y, ((-x^3*y^5 + x^3 - 2*x - 2)/(x^3*y^6)) dx),
 2: (((-2*x)/y^2) dx, 2/x*y^2, ((-2*x^3*y^3 + x^3 - 1)/(x^2*y^5)) dx),
 3: ((1/y^2) dx, 2/x^2*y^2, ((x^3*y^3 - 2*x^3 + 2*x - 2)/(x^3*y^5)) dx),
 4: ((1/y^3) dx, 0, (1/y^3) dx),
 5: (0 dx, 2/x*y^3, ((-2*x^3 - x - 1)/(x^2*y^4)) dx),
 6: ((1/y^4) dx, 0, (1/y^4) dx),
 7: ((2*x/y^4) dx, 2/x*y^4, ((2*x^3 - 2*x*y - y)/(x^2*y^4)) dx),
 8: ((1/y^5) dx, 0, (1/y^5) dx),
 9: ((x/y^5) dx, 0, (x/y^5) dx),
 10: ((1/y^6) dx, 0, (1/y^6) dx),
 11: ((x/y^6) dx, 0, (x/y^6) dx)}

In [113]:
RxRy.<x, y> = PolynomialRing(GF(p), 2)
w1 = superelliptic_cech(C, superelliptic_form(C, (1/y^5)), superelliptic_function(C, 0))
w2 = superelliptic_cech(C, superelliptic_form(C,2*x/y^4), superelliptic_function(C, 2/x*y^4))
w = w1+w2+w2

In [114]:
w.coordinates()

(((-x*y + 1)/y^5) dx, 4/x*y^4, ((-x^3*y + x*y^2 + x^2 - 2*y^2)/(x^2*y^5)) dx)


AttributeError: 'superelliptic_function' object has no attribute 'jth_coordinate'

In [65]:
a, b, c = C.degree_and_basis_de_rham()

In [7]:
licz = 0
m = 2
p = 5
R1.<x> = PolynomialRing(GF(p))
f = R1(x^3 + x + 4)
r = f.degree()
C = superelliptic(f, m, p)
for i in range(0, r):
    for j in range(1, m):
        omega = superelliptic_form(C, x^i/y^j)
        if (omega.is_regular_on_U0() and omega.is_regular_on_Uinfty()):
            print(omega)
            licz += 1
print(licz, C.genus())
print(C.basis_holomorphic_differentials())

NameError: name 'y' is not defined

In [ ]:
p = 5
R.<x, y> = PolynomialRing(GF(p), 2)
g = x^6*y^2 + y^2

In [83]:
omega = diffn(superelliptic_function(C, y^2))

In [84]:
omega.jth_component(0)

3*x^2 + 1

In [85]:
R.<x, y> = PolynomialRing(GF(p), 2)
g1 = x^3*y^7 + x^2*y^9
g2 = x^2*y + y^6
R1.<x> = PolynomialRing(GF(p))
R2 = FractionField(R1)
R3.<y> = PolynomialRing(R2)

xgcd(R3(g1), R3(g2))[1]*R3(g1) + xgcd(R3(g1), R3(g2))[2]*R3(g2)

y

In [86]:
H = HyperellipticCurve(x^5 - x + 1)

In [40]:
H

Hyperelliptic Curve over Finite Field of size 5 defined by y^2 = x^5 + 4*x + 1

In [84]:
f = x^3 + x + 2

In [86]:
f.derivative(x)

-2*x^2 + 1

In [3]:
p = 5
R1.<x> = PolynomialRing(GF(p))
R2 = FractionField(R1)
R3.<y> = PolynomialRing(R2)
g = y^2/x + y/(x+1)    
g = 1/y+x/y^2

In [4]:
R3.<z> = PolynomialRing(R2)
g(y = 1/z)

x*z^2 + z

In [57]:
f

x^3 + x + 4

In [62]:
f.coefficient()

AttributeError: 'sage.rings.polynomial.polynomial_zmod_flint.Polynomial_zmod_flint' object has no attribute 'coefficient'

In [35]:
x^3+x+1

x^3 + x + 1

In [36]:
parent(x)

Symbolic Ring

In [37]:
R.<x> = PolynomialRing(GF(5))

In [39]:
R = (x^3+x).parent()

In [44]:
R.<x, y> = PolynomialRing(GF(5))
RR = FractionField(R)
A = RR(1/(x*y))

In [45]:
A.derivative(x)

(-1)/(x^2*y)

In [42]:
dict1 = {}
dict1[3] = 5
dict1[6] = 121

In [46]:
degrees1_inv = {b:a for a, b in dict1.items()}

In [47]:
degrees1_inv

{5: 3, 121: 6}